### Module imports

In [ ]:
import base64
import os
import sys

# Process control
import threading
from skfuzzy import control as ctrl

# Process monitoring
from datetime import date, datetime
import time
import csv

# Virtual sensor
import joblib
import pandas as pd

# CV model
import numpy as np
import cv2
from ultralytics import YOLO
from skimage.filters import threshold_multiotsu
import shutil
import matplotlib.pyplot as plt

### Variable Inits

In [ ]:
def init_variables():
    xgb_mod = joblib.load('monitoring\\xgb_model.pkl')
    print("Virtual sensor model loaded")
    closed_fuzzy_system = joblib.load('fuzzy_tools\\closed_fuzzy_sets.pkl')

    # # Export sollte direkt der controller sein und nicht das System, welches erst noch simuliert werden muss
    closed_controller = ctrl.ControlSystemSimulation(closed_fuzzy_system)

    # Virtual sensor initial and default inputs #
    x_actual = {
        'rel. humidity (%)' : [],
        'Air temperature (°C)' : [],
        'Fan speed (rpm)' : []
    }
    x_actual = pd.DataFrame(x_actual)
    x_actual['rel. humidity (%)'] = [40]
    x_actual['Air temperature (°C)'] = [60]
    x_actual['Fan speed (rpm)'] = [2000]
    
    # ##########################
    # # Params
    # # Default machine parameters
    str_yolo = 'test'
    str_segmentation = 'test1'
    switch = 1
    stop_event = threading.Event()

    # User interface default inputs
    d_error = 0.0
    l_dry = 0.8 
    param_v_band = 2.6
    v_band = (param_v_band) / 60
    d_wet = 5

    # Control parameters default inputs
    d_target = 4.0
    d_error_max = 0.5
    max_cycles = 5
    t_c = l_dry / v_band #cycle time is part dwell time in drying zone
    t_c_mon = 0.5 * t_c

    # Process parameters initial values
    param = [('n_UL', 2000), ('T_dry', 50)]
    p_current = 1.0
    parts = 0 
    part = 'fuehrungsscheibe'

    new = True

    # Process monitoring initial values
    d_pred = 0
    dryness = []
    total_dryness = 0
    dry_dict = {
        0: "1.0",
        1: "1.5",
        2: "2.0",
        3: "2.5",
        4: "3.0",
        5: "3.5",
        6: "4.0",
        7: "4.5"
    }

    # FLC control-bools init #
    ctrl_active = True
    stop_ctrl = False
    cascade = False
    mtr_active = True
    parts_in_zone = True

    lock = threading.Lock()

    inter_count = 0
    class CircularList:
        def __init__(self, size):
            self.size = size
            self.values = []

        def add_value(self, value):
            if len(self.values) < self.size:
                self.values.append(value)
                print(value)
            else:
                self.values.pop(0)
                self.values.append(value)
        def total_sum(self):
            return sum(self.values)

    log_n = CircularList(t_c_mon)
    log_phi = CircularList(t_c_mon)
    log_rh = CircularList(t_c_mon)

    flc_control_mode_active = False
    algo_mode_active = False
    ready = True
    semi_state_auto = False

    return xgb_mod, closed_fuzzy_system, closed_controller, x_actual, str_yolo, str_segmentation, switch, stop_event, d_error, l_dry, param_v_band, d_wet, d_target, d_error_max, max_cycles, param, v_band, t_c, t_c_mon, p_current, parts, part, new, d_pred, dryness, total_dryness, dry_dict, ctrl_active, stop_ctrl, cascade, mtr_active, parts_in_zone, lock, inter_count, CircularList, log_n, log_phi, log_rh, flc_control_mode_active, algo_mode_active, ready, semi_state_auto

### Process monitoring functions

In [ ]:
def total_sum(self):
    return total_sum(self.values)

def average():
    global log_n, log_phi, log_rh, t_c_mon
    n_mean = log_n.total_sum()/t_c_mon
    phi_mean = log_phi.total_sum()/t_c_mon
    rh_mean = log_rh.total_sum()/t_c_mon
    return n_mean, phi_mean, rh_mean

def calc_error(d_pred):
    global d_target
    n_mean, phi_mean, rh_mean = average()
    print('n_mean: ', round(n_mean, 2))
    print('phi_mean: ', round(phi_mean, 2))
    print('rh_mean: ', round(rh_mean, 2))
    data = {
        'rel. humidity (%)': [rh_mean],
        'Air temperature (°C)': [phi_mean],
        'Fan speed (rpm)': [n_mean]
    }
    print('d_target for calculating d_error:', d_target)
    if d_pred is not None:
        print("d_pred: ", d_pred)
        d_error = d_pred - d_target
        print('d_error from calc_error() func without [0]:', d_error)
    else:
        d_error = None
        print("d_pred is not yet available for calc_error().")
    return d_error

def monitor_error():
    global stop_event
    refresh_IR_frames()
    while not stop_event.is_set():
        global ctrl_active, mtr_active, d_error, x_actual, stop_ctrl, parts_in_zone, d_target
        # If off
        print("monitor_error func was started!")
        
        while mtr_active and parts_in_zone:#ctrl_active and 
            print("Monitor while loop was started")
            # retrieve drying conditions as array and calculate predicted dryness and dryness error, store in x_actual
            x_actual = opcua_client.get_values([opc_node_TZ_rH_read, opc_node_T_UTR_op, opc_node_n_UL_op])

            if d_pred is not None:
                d_error = calc_error(d_pred)
                print('d_error from monitor_error() func: ', d_error)

                # Get the current timestamp
                timestamp = datetime.now().strftime('%Y-%m-%d %H:%M:%S')

                # Construct the full path to the CSV file
                filepath = os.path.join('C:\\lotus-expertensystem\\data', 'log_d.csv')

                # Check if the file already exists to determine if the header needs to be written
                write_header = not os.path.exists(filepath)

                with open(filepath, 'a', newline='') as csvfile:
                    csvwriter = csv.writer(csvfile)
                    print('logging dryness data')
                    # Write header row if the file is newly created
                    if write_header:
                        csvwriter.writerow(['Timestamp', 'd_target', 'd_pred', 'd_error', 'monitor status'])
                                
                    csvwriter.writerow([timestamp, d_target, (d_target + d_error), d_error, mtr_active])

                print('d_error from monitor_error() func: ', d_error)
                if (flc_control_mode_active ==  True):
                    if abs(d_error) > d_error_max:
                        print("d_error > d_error_max in monitor_error func!")
                        with lock:
                            stop_ctrl = False
                            cascading(d_error)
                            print('cascading() started.')
                            #mtr_active = False
                            print("Monitor wurde geschlossen!")
            else:
                print("monitor_error() waiting for d_pred to become available.")
            time.sleep(t_c_mon)
                            
    return d_error

### Process control functions

In [ ]:
def closed_fuzzy_controller(para, sp_current, d_error):
    global cascade, ctrl_active, stop_ctrl, mtr_active, d_target
    with lock:
        cascade = False
    cycle_count = 0

    while ((not cascade) and (not stop_ctrl)):
        print("Fuzzy logic func was started!")
        closed_controller.input['error'] = d_error
        print("This is the calculated d_error: " + str(d_error))
        closed_controller.compute()
        p = closed_controller.output['output']
        print("p: ", p)
        print("d_error: ", d_error)
        sp_current_value = sp_current[0]
        sp_current_value = sp_current_value[0]
        #p_current_value = p_current_value[0]
        print('p_current_value: ', sp_current_value)
        sp_current_min = sp_current[1]
        # p_current_min = p_current_min[0]
        sp_current_max = sp_current[2]
        # p_current_max = p_current_max[0]
        sp_new = p * sp_current_value # (init with dict "param")

        if sp_new > sp_current_max:
            sp_new = sp_current_max
            print("sp_new is larger than the max. operation value, the max. value was passed!")
        if sp_new < sp_current_min:
            sp_new = sp_current_min
            print("sp_new is smaller than the min. operation value, the min. value was passed!")
        print("new setpoint: ", sp_new)
        #if sp_new<=p_current_max and sp_new >=p_current_min:
        # update actual setpoint (current_param) with new setpoint (current_param_new)
        print(f"new setpoint for {para}: {sp_new}")
        if para == "n_UL":
            var = opcua_client.get_node(opc_node_UTR_bAlgPerm)
            var.set_attribute(ua.AttributeIds.Value, ua.DataValue(True))
            var = opcua_client.get_node(opc_node_UTR_bAlgorithmModeActivated)
            var.set_attribute(ua.AttributeIds.Value, ua.DataValue(True))

            var = opcua_client.get_node(opc_node_n_UL_set)
            var.set_attribute(ua.AttributeIds.Value, ua.DataValue(ua.Variant(sp_new, ua.VariantType.Float)))

        if para == "T_dry":
            var = opcua_client.get_node(opc_node_Heiz_UL_bSetStatusOnAlgorithm)
            var.set_attribute(ua.AttributeIds.Value, ua.DataValue(True))
            var = opcua_client.get_node(opc_node_Heiz_UL_bAlgorithmModeActivated)
            var.set_attribute(ua.AttributeIds.Value, ua.DataValue(True))

            var = opcua_client.get_node(opc_node_T_UTR_set)
            var.set_attribute(ua.AttributeIds.Value, ua.DataValue(ua.Variant(sp_new, ua.VariantType.Float)))
            
            # var = opcua_client.get_node(opc_node_v_Band_UTR_set)
            # var.set_attribute(ua.AttributeIds.Value, ua.DataValue(ua.Variant(p_current_value[3], ua.VariantType.Float)))

        sp_current = [[sp_new], sp_current_min, sp_current_max]
        sp_current_value = sp_current[0]
        sp_current_value = sp_current_value[0]
        print('sp_current: ', sp_current_value)

        # Get the current timestamp
        timestamp = datetime.now().strftime('%Y-%m-%d %H:%M:%S')

        # Construct the full path to the CSV file
        filepath = os.path.join('C:\\lotus-expertensystem\\data', 'log_ctrl.csv')

        # Check if the file already exists to determine if the header needs to be written
        write_header = not os.path.exists(filepath)

        with open(filepath, 'a', newline='') as csvfile:
            csvwriter = csv.writer(csvfile)
            print('logging controller actions')
            # Write header row if the file is newly created
            if write_header:
                csvwriter.writerow(['Timestamp', 'man. variable', 'current setpoint'])
            
            csvwriter.writerow([timestamp, para, sp_current_value])
        
        cycle_count += 1
        time.sleep(t_c_mon)
        # nach time_sleep neue Abweichung berechnen
        d_error = calc_error(d_pred)
        if abs(d_error) < d_error_max:
            with lock:
                stop_ctrl = True
            print(f"residual error: {d_error}")
            print('\n stop_ctrl = True')
                    
        if cycle_count == max_cycles:
            with lock:
                cascade = True
            print(f"residual error: {d_error}")
            print('\n cascade = True')

def cascading(d_error):
    global stop_event
    while not stop_event.is_set():
        global mtr_active, ctrl_active, x_actual, stop_ctrl
        while ctrl_active:
            print('stop_ctrl: ', stop_ctrl)
            while parts_in_zone and not stop_ctrl:
                print("Starting cascaded closed-loop fuzzy controller...")
                # retrieve actual drying system setpoints
                n_UL_sp = opcua_client.get_values([opc_node_n_UL_set])
                T_dry_sp = opcua_client.get_values([opc_node_T_UTR_op]) #opc_node_T_UTR_set
                print("n_UL: ", n_UL_sp)
                print("T_dry_sp: ", T_dry_sp)
                param_pos = {
                        "n_UL": [n_UL_sp, 870, 3500],
                        "T_dry": [T_dry_sp, 30, 110] # T_dry_sp, 
                }
                param_neg = {
                        "T_dry": [T_dry_sp, 30, 110],
                        "n_UL": [n_UL_sp, 870, 3500]
                }
                if d_error > 0:
                    print('d_error > 0 in cascading()')
                    for key, value in param_pos.items(): # iterate through each setpoint in params (n_UL, T_dry)
                        print(key)
                        closed_fuzzy_controller(key, value, d_error)
                if d_error < 0:
                    print('d_error < 0 in cascading()')
                    for key, value in param_neg.items(): # iterate through each setpoint in params (T_dry, n_UL)
                        print(key)
                        closed_fuzzy_controller(key, value, d_error)
                with lock:
                    stop_ctrl  = True
                    mtr_active = True
                monitor = threading.Thread(target=monitor_error)
                monitor.start() 
            # Get the current timestamp
            timestamp = datetime.now().strftime('%Y-%m-%d %H:%M:%S')
            # Construct the full path to the CSV file
            filepath = os.path.join('C:\\lotus-expertensystem\\data', 'log_ctrl_status.csv')
            # Check if the file already exists to determine if the header needs to be written
            write_header = not os.path.exists(filepath)
            with open(filepath, 'a', newline='') as csvfile:
                csvwriter = csv.writer(csvfile)
                print('logging controller status')
                # Write header row if the file is newly created
                if write_header:
                    csvwriter.writerow(['Timestamp', 'status controller', 'stop controller'])  
                csvwriter.writerow([timestamp, ctrl_active, stop_ctrl])
            time.sleep(t_c_mon)
            print("Closed-loop fuzzy controller stopped.\n\n\n\n\n\n\n")
            monitor = threading.Thread(target=monitor_error) # args fehlen
            monitor.start() 
            with lock:
                mtr_active = True # reactivate monitor after stopping control

### Part detection and image adjustment functions

In [ ]:
def subtract_median(image_path):
    image = cv2.imread(image_path, cv2.IMREAD_GRAYSCALE)
    _, thresholded = cv2.threshold(image, 254, 255, cv2.THRESH_BINARY_INV)
    image = cv2.bitwise_and(image, image, mask=thresholded)
    mask = image > 0
    min_t = np.min(image[mask])
    lower_b = np.array([min_t], dtype=np.uint8)
    upper_b = np.array([min_t+50], dtype=np.uint8)
    mask = cv2.inRange(image, lower_b, upper_b)
    median_int = np.median(image[mask])
    # Schwellenwert auf das ursprüngliche Bild anwenden
    result = image-median_int
    return result

def read_parts_in_zone():
    global parts, parts_in_zone, inter_count
    inter_count = inter_count + 1
    x_actual = opcua_client.get_values([opc_node_TZ_rH_read, opc_node_T_UTR_op, opc_node_n_UL_op])
    log_rh.add_value(x_actual[0])
    log_phi.add_value(x_actual[1])
    log_n.add_value(x_actual[2])
    upc_parts_counter = opcua_client.get_values([opc_node_werkstueckzaehler])
    upc_parts_counter = upc_parts_counter[0]
    if parts < upc_parts_counter:
        with lock:
            parts_in_zone = True    
    inter_count = 0
    if inter_count >= (60*10):
        with lock:
            parts_in_zone = False

def semi_circle_detection(path):
    # Load data
    img = cv.imread(path, cv.IMREAD_COLOR)

    # Convert image (method: RGB2GRAY)
    gray = cv.cvtColor(img, cv.COLOR_BGR2GRAY)

    # Filter image (method: bilateral)
    bilateral = cv.bilateralFilter(gray, 5,15,15)

    # Additional filtering (method: canny, maybe obsolete
    canny = cv.Canny(bilateral,10,30)
    # Initialise counters for recognized incoming and outgoing parts
    incoming = 0
    outgoing = 0

    # Detection of circles
    circles = cv.HoughCircles(canny, cv.HOUGH_GRADIENT, 1, 100, param1=200, param2=40, minRadius=60, maxRadius=100)
    #
    if circles is not None:
        circles = np.uint16(np.around(circles))
        for i in circles[0, :]: # i ist die Anzahl der erkannten Kreise
            center = (i[0], i[1]) # Extrahieren der Koordinaten des Kreismittelpunktes
            x = i[0] # x-Koordinate des centers des erkannten Kreises
            y = i[1] # y-Koordinate des centers des erkannten Kreises

            # # draw circle outline
            radius = i[2] # auslesen des Radiuses

            if (288*0.5 > y): # Checking for outgoing part
                outgoing = outgoing + 1
                return False
            elif (288*0.5 < y): # Checking for incoming part
                incoming = incoming + 1

                return True
            else:
                return False

    # List of legal and illegal states
    # Programm ausdenken, welches erkennt welcher Status gerade herrscht. 
    # 1 -> One part entering zone, no other parts in frame  -> legal
    # 2 -> No parts in frame                                -> legal
    # 3 -> One part entering zone, one other part in frame  -> illegal
    # 4 -> One part exiting zone, no other parts in frame   -> legal
    # 5 -> One part exiting zone, one other part in frame   -> illegal
    # 6 -> One part entering, one other part exiting zone   -> legal
    # debug_const = 1; # Line only for debugging purposes